In [ ]:
#PREPROCESSING

import cv2
import numpy as np
import os
import matplotlib.pyplot as plt

# Load the Haar Cascade for face detection
haar_cascade_path = cv2.data.haarcascades + 'haarcascade_frontalface_default.xml'
face_cascade = cv2.CascadeClassifier(haar_cascade_path)

if face_cascade.empty():
    print("Error: Haar Cascade XML not found.")
    exit()

buffer_width = 8  # Horizontal buffer
buffer_height = 8  # Vertical buffer
solid_color = [255, 0, 0]  # Solid color to replace faces (blue)

# Function to preprocess a single frame/image
def preprocess_frame(image):
    # Step 1: Denoise using Bilateral Filter
    denoised_image = cv2.bilateralFilter(image, 9, 75, 75)
    
    # Step 2: Sharpen the image using Gaussian Blur and Unsharp Masking
    blurred_image = cv2.GaussianBlur(denoised_image, (5, 5), 1.5)
    sharpening_kernel = np.array([[-1, -1, -1],
                                  [-1,  9, -1],
                                  [-1, -1, -1]])
    sharpened_image = cv2.filter2D(blurred_image, -1, sharpening_kernel)
    
    # Step 3: Enhance brightness and contrast using Histogram Equalization
    ycrcb_image = cv2.cvtColor(sharpened_image, cv2.COLOR_BGR2YCrCb)
    y, cr, cb = cv2.split(ycrcb_image)
    y = cv2.equalizeHist(y)
    enhanced_image = cv2.merge([y, cr, cb])
    enhanced_image = cv2.cvtColor(enhanced_image, cv2.COLOR_YCrCb2BGR)
    
    # Step 4: Convert to grayscale for face detection
    gray_image = cv2.cvtColor(enhanced_image, cv2.COLOR_BGR2GRAY)
    
    # Step 5: Detect faces using Haar Cascade
    faces = face_cascade.detectMultiScale(gray_image, scaleFactor=1.1, minNeighbors=5, minSize=(30, 30))
    face_removed_image = enhanced_image.copy()
    mask = np.zeros_like(image)
    
    for (x, y, w, h) in faces:
        # Define region to remove (face + buffer)
        x_start = max(x - buffer_width, 0)
        y_start = max(y - buffer_height, 0)
        x_end = min(x + w + buffer_width, image.shape[1])
        y_end = min(y + h + buffer_height, image.shape[0])

        # Update the mask and replace the region with a solid color
        mask[y_start:y_end, x_start:x_end] = [255, 255, 255]  # White mask for visualization
        face_removed_image[y_start:y_end, x_start:x_end] = solid_color  # Replace with solid color
    
    # Step 6: Convert to YCbCr for skin detection
    ycrcb_image = cv2.cvtColor(face_removed_image, cv2.COLOR_BGR2YCrCb)
    
    # Step 7: Define skin color range and create a skin mask
    lower_skin = np.array([0, 133, 77])
    upper_skin = np.array([255, 173, 127])
    skin_mask = cv2.inRange(ycrcb_image, lower_skin, upper_skin)
    
    # Step 8: Apply morphological operations to refine the mask
    kernel_morph = np.ones((5, 5), np.uint8)
    dilated_image = cv2.dilate(skin_mask, kernel_morph, iterations=1)
    eroded_image = cv2.erode(dilated_image, kernel_morph, iterations=1)
    
    # Step 9: Remove small components (less than 400 pixels)
    num_labels, labels, stats, _ = cv2.connectedComponentsWithStats(eroded_image, connectivity=8)
    refined_mask = np.zeros_like(eroded_image)
    
    for i in range(1, num_labels):  # Skip background label 0
        if stats[i, cv2.CC_STAT_AREA] >= 1700:
            refined_mask[labels == i] = 255
    
    return blurred_image, sharpened_image, enhanced_image, face_removed_image, skin_mask, dilated_image, eroded_image, refined_mask

# Path to the image folder
image_folder = r'C:\Users\dell\Desktop\GESTURE PROJECT\Datasets\Hand_Gesture_RGB_Frames\Hand_Gesture_RGB_Frames\0499\03_01_0499_(16_05_18_16_29_35)_c'

# Read and process all images in the folder
image_files = sorted([f for f in os.listdir(image_folder) if f.endswith('.jpg')])

# Loop through images and process them
for image_file in image_files:
    image_path = os.path.join(image_folder, image_file)
    image = cv2.imread(image_path)
    
    if image is None:
        print(f"Error: Image not loaded. Skipping: {image_file}")
        continue
    
    blurred_image, sharpened_image, enhanced_image, face_removed_image, skin_mask, dilated_image, eroded_image, refined_mask = preprocess_frame(image)
    
    # Convert images to RGB for Matplotlib
    images = [image, blurred_image, sharpened_image, enhanced_image, face_removed_image, skin_mask, dilated_image, eroded_image, refined_mask]
    titles = ['Original', 'Blurred', 'Sharpened', 'Enhanced', 'Face Removed', 'Skin Mask', 'Dilated', 'Eroded', 'Refined Mask']
    
    plt.figure(figsize=(14, 10))
    for i, (img, title) in enumerate(zip(images, titles), 1):
        plt.subplot(3, 3, i)
        if len(img.shape) == 2:
            plt.imshow(img, cmap='gray')
        else:
            plt.imshow(cv2.cvtColor(img, cv2.COLOR_BGR2RGB))
        plt.title(title)
        plt.axis('off')
    
    plt.show()


In [ ]:
#MAJOR AND MINOR AXIS

import cv2
import numpy as np
import os
import matplotlib.pyplot as plt

# Load the Haar Cascade for face detection
haar_cascade_path = cv2.data.haarcascades + 'haarcascade_frontalface_default.xml'
face_cascade = cv2.CascadeClassifier(haar_cascade_path)

if face_cascade.empty():
    print("Error: Haar Cascade XML not found.")
    exit()

buffer_width = 8  # Horizontal buffer
buffer_height = 8  # Vertical buffer
solid_color = [255, 0, 0]  # Solid color to replace faces (blue)

def preprocess_frame(image):
    denoised_image = cv2.bilateralFilter(image, 9, 75, 75)
    blurred_image = cv2.GaussianBlur(denoised_image, (5, 5), 1.5)
    sharpening_kernel = np.array([[-1, -1, -1],
                                  [-1,  9, -1],
                                  [-1, -1, -1]])
    sharpened_image = cv2.filter2D(blurred_image, -1, sharpening_kernel)
    ycrcb_image = cv2.cvtColor(sharpened_image, cv2.COLOR_BGR2YCrCb)
    y, cr, cb = cv2.split(ycrcb_image)
    y = cv2.equalizeHist(y)
    enhanced_image = cv2.merge([y, cr, cb])
    enhanced_image = cv2.cvtColor(enhanced_image, cv2.COLOR_YCrCb2BGR)
    gray_image = cv2.cvtColor(enhanced_image, cv2.COLOR_BGR2GRAY)
    faces = face_cascade.detectMultiScale(gray_image, scaleFactor=1.1, minNeighbors=5, minSize=(30, 30))
    face_removed_image = enhanced_image.copy()
    mask = np.zeros_like(image)
    
    for (x, y, w, h) in faces:
        x_start = max(x - buffer_width, 0)
        y_start = max(y - buffer_height, 0)
        x_end = min(x + w + buffer_width, image.shape[1])
        y_end = min(y + h + buffer_height, image.shape[0])
        mask[y_start:y_end, x_start:x_end] = [255, 255, 255]
        face_removed_image[y_start:y_end, x_start:x_end] = solid_color
    
    ycrcb_image = cv2.cvtColor(face_removed_image, cv2.COLOR_BGR2YCrCb)
    lower_skin = np.array([0, 133, 77])
    upper_skin = np.array([255, 173, 127])
    skin_mask = cv2.inRange(ycrcb_image, lower_skin, upper_skin)
    kernel_morph = np.ones((5, 5), np.uint8)
    dilated_image = cv2.dilate(skin_mask, kernel_morph, iterations=1)
    eroded_image = cv2.erode(dilated_image, kernel_morph, iterations=1)
    num_labels, labels, stats, _ = cv2.connectedComponentsWithStats(eroded_image, connectivity=8)
    refined_masks = []
    
    for i in range(1, num_labels):
        if stats[i, cv2.CC_STAT_AREA] >= 1700:
            component_mask = np.zeros_like(eroded_image)
            component_mask[labels == i] = 255
            refined_masks.append((component_mask, stats[i]))
    
    return refined_masks

def detect_axes(mask, stats):
    contours, _ = cv2.findContours(mask, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    if not contours:
        return mask, None, mask
    
    contour_image = cv2.cvtColor(mask, cv2.COLOR_GRAY2BGR)
    max_contour = max(contours, key=cv2.contourArea)
    points = max_contour.squeeze()
    
    major_axis = None
    max_distance = 0
    axis_direction = None  # Store direction
    
    for i in range(len(points)):
        for j in range(i + 1, len(points)):
            dist = np.linalg.norm(points[i] - points[j])
            if dist > max_distance:
                max_distance = dist
                major_axis = (tuple(points[i]), tuple(points[j]))
    
    processed_mask = mask.copy()
    
    if major_axis:
        cv2.line(contour_image, major_axis[0], major_axis[1], (255, 0, 0), 2)
        
        # Determine if the major axis is vertical or horizontal
        x1, y1 = major_axis[0]
        x2, y2 = major_axis[1]
        
        if abs(y2 - y1) > abs(x2 - x1):
            axis_direction = "Vertical"
            half_height = stats[cv2.CC_STAT_HEIGHT] // 2
            y_start = stats[cv2.CC_STAT_TOP]
            y_end = y_start + half_height
            processed_mask[y_end:, :] = 0  # Remove lower half of the component
        else:
            axis_direction = "Horizontal"
    
    return contour_image, axis_direction, processed_mask

image_folder = r'C:\Users\dell\Desktop\GESTURE PROJECT\Datasets\Hand_Gesture_RGB_Frames\Hand_Gesture_RGB_Frames\0500\03_01_0500_(03_10_18_20_42_26)_c'
image_files = sorted([f for f in os.listdir(image_folder) if f.endswith('.jpg')])

for image_file in image_files:
    image_path = os.path.join(image_folder, image_file)
    image = cv2.imread(image_path)
    
    if image is None:
        print(f"Error: Image not loaded. Skipping: {image_file}")
        continue
    
    refined_masks = preprocess_frame(image)
    
    for idx, (refined_mask, stats) in enumerate(refined_masks):
        axis_image, axis_direction, processed_mask = detect_axes(refined_mask, stats)
        print(f"{image_file} - Component {idx + 1}: Major Axis - {axis_direction}")
        
        #plt.figure(figsize=(10, 5))
        #plt.subplot(1, 3, 1)
        #plt.imshow(refined_mask, cmap='gray')
        #plt.title(f'Refined Mask {idx + 1}')
        #plt.axis('off')
        
        #plt.subplot(1, 3, 2)
        #plt.imshow(axis_image)
        #plt.title(f'Major Axis: {axis_direction}')
        #plt.axis('off')
        
        plt.subplot(1, 3, 3)
        plt.imshow(processed_mask, cmap='gray')
        #plt.title('Processed Component')
        plt.axis('off')
        
        plt.show()
